# 🏛️ Harvard’s Artifacts Collection: ETL, SQL Analytics & Streamlit Showcase

## Domain : Cultural Heritage Data Analytics / Museum Informatics



### API Integration & Data Extraction


In [4]:
import streamlit as st
harvard_api = st.secrets.get("harvard")["api_key"]
if not harvard_api:
    st.error("API key for Harvard not found in secrets.")
    st.stop()
url='https://api.harvardartmuseums.org/classification'
import requests
parameters={'apikey':harvard_api,
           'size':100}
response= requests.get(url, parameters)
response

<Response [200]>

In [5]:
data=response.json()
data

{'info': {'totalrecordsperquery': 100,
  'totalrecords': 64,
  'pages': 1,
  'page': 1,
  'responsetime': '4 ms'},
 'records': [{'objectcount': 1,
   'name': 'Natural History Specimens',
   'id': 1133,
   'lastupdate': '2025-10-17T04:03:17-04:00',
   'classificationid': 1133},
  {'objectcount': 1,
   'name': 'Paintings with Text',
   'id': 197,
   'lastupdate': '2025-10-17T04:03:17-04:00',
   'classificationid': 197},
  {'objectcount': 66,
   'name': 'Performance Artifacts',
   'id': 224,
   'lastupdate': '2025-10-17T04:03:17-04:00',
   'classificationid': 224},
  {'objectcount': 1,
   'name': 'Text',
   'id': 204,
   'lastupdate': '2025-10-17T04:03:17-04:00',
   'classificationid': 204},
  {'objectcount': 80,
   'name': 'Tokens',
   'id': 492,
   'lastupdate': '2025-10-17T04:03:17-04:00',
   'classificationid': 492},
  {'objectcount': 62,
   'name': 'Brick Stamps',
   'id': 304,
   'lastupdate': '2025-10-17T04:03:17-04:00',
   'classificationid': 304},
  {'objectcount': 46,
   'name':

In [6]:
from collections import Counter
classiresults= [record['name']
                for record in data['records']
                if record.get('objectcount',0) >= 2500]
print('name with object count >= 2500:')
for name in classiresults:
    print(name)

name with object count >= 2500:
Accessories (non-art)
Photographs
Drawings
Prints
Paintings
Sculpture
Coins
Vessels
Textile Arts
Archival Material
Fragments
Manuscripts
Seals
Straus Materials


In [7]:
url = 'https://api.harvardartmuseums.org/object'
all_records = []   
classifications = ["Paintings", "Sculpture", "Drawings", "Fragments", "Photographs"]
for classi in classifications:
    print(f"\nFetching classification: {classi}")
    for page in range(1, 26):
        parameters = {
            'apikey': harvard_api,
            'size': 100,
            'page': page,
            'classification': classi
        }
        response = requests.get(url, parameters)
        data = response.json()
        all_records.extend(data['records'])
    print(f"Total collected so far: {len(all_records)}")



Fetching classification: Paintings
Total collected so far: 2500

Fetching classification: Sculpture
Total collected so far: 5000

Fetching classification: Drawings
Total collected so far: 7500

Fetching classification: Fragments
Total collected so far: 10000

Fetching classification: Photographs
Total collected so far: 12500


In [8]:
data['records']

[{'copyright': None,
  'contextualtextcount': 0,
  'creditline': 'Harvard Art Museums/Fogg Museum, Transfer from the Carpenter Center for the Visual Arts, American Professional Photographers Collection',
  'accesslevel': 1,
  'createdate': '2002-11-01T00:00:00-05:00',
  'dateoflastpageview': '2019-04-02',
  'classificationid': 17,
  'division': 'Modern and Contemporary Art',
  'markscount': 0,
  'publicationcount': 0,
  'totaluniquepageviews': 1,
  'contact': 'am_moderncontemporary@harvard.edu',
  'colorcount': 9,
  'rank': 40001,
  'id': 120504,
  'state': None,
  'verificationleveldescription': 'Adequate. Object is adequately described but information may not be vetted',
  'period': None,
  'images': [{'date': '2008-01-23',
    'copyright': 'President and Fellows of Harvard College',
    'imageid': 286768,
    'idsid': 20430379,
    'format': 'image/jpeg',
    'description': None,
    'technique': None,
    'renditionnumber': 'INV173483N',
    'displayorder': 1,
    'baseimageurl': '

In [9]:
print(type(data['records']))

<class 'list'>


In [10]:
data['records'][0]

{'copyright': None,
 'contextualtextcount': 0,
 'creditline': 'Harvard Art Museums/Fogg Museum, Transfer from the Carpenter Center for the Visual Arts, American Professional Photographers Collection',
 'accesslevel': 1,
 'createdate': '2002-11-01T00:00:00-05:00',
 'dateoflastpageview': '2019-04-02',
 'classificationid': 17,
 'division': 'Modern and Contemporary Art',
 'markscount': 0,
 'publicationcount': 0,
 'totaluniquepageviews': 1,
 'contact': 'am_moderncontemporary@harvard.edu',
 'colorcount': 9,
 'rank': 40001,
 'id': 120504,
 'state': None,
 'verificationleveldescription': 'Adequate. Object is adequately described but information may not be vetted',
 'period': None,
 'images': [{'date': '2008-01-23',
   'copyright': 'President and Fellows of Harvard College',
   'imageid': 286768,
   'idsid': 20430379,
   'format': 'image/jpeg',
   'description': None,
   'technique': None,
   'renditionnumber': 'INV173483N',
   'displayorder': 1,
   'baseimageurl': 'https://nrs.harvard.edu/urn-

In [11]:
artifact_metadata = []
artifact_media = []
artifact_colors = []
for i in all_records:
    artifact_metadata.append(dict(
        id = i['id'],
        title = i['title'],
        culture = i['culture'],
        period = i['period'],
        century = i['century'],
        medium = i['medium'],
        dimensions = i['dimensions'],
        description = i['description'],
        department = i['department'],
        classification = i['classification'],
        accessionyear = i['accessionyear'],
        accessionmethod = i['accessionmethod']))
    artifact_media.append(dict(
        objectid = i['objectid'],
        imagecount = i['imagecount'],
        mediacount = i['mediacount'],
        colorcount = i['colorcount'],
        rank_value = i['rank'],
        datebegin = i['datebegin'],
        dateend = i['dateend']))
    color_details = i.get('colors')
    if color_details:
        for j in color_details:
            artifact_colors.append(dict(
                objectid = i['objectid'],
                color = j['color'],
                spectrum = j['spectrum'],
                hue = j['hue'],
                percent = j['percent'],
                css3 = j['css3']))


In [12]:
print("Metadata:", len(artifact_metadata))
print("Media:", len(artifact_media))
print("Colors:", len(artifact_colors))


Metadata: 12500
Media: 12500
Colors: 85823


## Connecting Python with MySQL

In [13]:
import mysql.connector

In [14]:
connection = mysql.connector.connect(
    host=st.secrets["database"]["db_host"],
    user=st.secrets["database"]["db_user"],
    password=st.secrets["database"]["db_pass"],
    database=st.secrets["database"]["db_name"]
)
cursor = connection.cursor()
print("MySQL server established")


MySQL server established


## Creating Database

In [15]:
cursor.execute('CREATE DATABASE IF NOT EXISTS harvard_artifacts;')
cursor.execute("USE harvard_artifacts;")
print("Database ready: harvard_artifacts")

Database ready: harvard_artifacts


## Creating Tables in DB 'harvard_artifacts'

In [16]:
cursor.execute("""
CREATE TABLE IF NOT EXISTS artifact_metadata (
  id INT PRIMARY KEY,
  title TEXT,
  culture TEXT,
  period TEXT,
  century TEXT,
  medium TEXT,
  dimensions TEXT,
  description TEXT,
  department TEXT,
  classification TEXT,
  accessionyear INT,
  accessionmethod TEXT
);
""")

cursor.execute("""
CREATE TABLE IF NOT EXISTS artifact_media (
  objectid INT PRIMARY KEY,
  imagecount INT,
  mediacount INT,
  colorcount INT,
  rank_value INT,
  datebegin INT,
  dateend INT,
  CONSTRAINT fk1_id FOREIGN KEY (objectid) REFERENCES artifact_metadata(id)
);
""")

cursor.execute("""
CREATE TABLE IF NOT EXISTS artifact_colors (
  objectid INT,
  color TEXT,
  spectrum TEXT,
  hue TEXT,
  percent REAL,
  css3 TEXT,
  CONSTRAINT fk2_id FOREIGN KEY (objectid) REFERENCES artifact_metadata(id)
);
""")
connection.commit()
print('tables created successfully')

tables created successfully


### Deleting old data for fresh insert

In [17]:
cursor.execute("DELETE FROM artifact_colors;")
cursor.execute("DELETE FROM artifact_media;")
cursor.execute("DELETE FROM artifact_metadata;")
connection.commit()
print('old data deleted for fresh insert')

old data deleted for fresh insert


## Inserting Values in the respective tables

In [18]:
insert_metadata = """ 
INSERT INTO artifact_metadata ( id, title, culture, period, century, medium, dimensions, description, 
department, classification, accessionyear, accessionmethod ) 
VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s) 
"""
cursor.executemany(insert_metadata, [(
    r.get('id'), 
    r.get('title'), 
    r.get('culture'), 
    r.get('period'), 
    r.get('century'),
    r.get('medium'), 
    r.get('dimensions'), 
    r.get('description'), 
    r.get('department'),
    r.get('classification'), 
    r.get('accessionyear'), 
    r.get('accessionmethod')
) for r in artifact_metadata])
connection.commit()

In [19]:
insert_media = """
INSERT INTO artifact_media (
    objectid, imagecount, mediacount, colorcount, rank_value, datebegin, dateend
) VALUES (%s, %s, %s, %s, %s, %s, %s)
"""
cursor.executemany(insert_media, [(
            r.get('objectid'),
            r.get('imagecount'),
            r.get('mediacount'),
            r.get('colorcount'),
            r.get('rank_value'),  
            r.get('datebegin'),
            r.get('dateend')
        )for r in artifact_media])
connection.commit()


In [20]:
insert_colors = """
INSERT INTO artifact_colors (
    objectid, color, spectrum, hue, percent, css3
) VALUES (%s, %s, %s, %s, %s, %s)
"""
cursor.executemany(insert_colors,[(
            r.get('objectid'),
            r.get('color'),
            r.get('spectrum'),
            r.get('hue'),
            r.get('percent'),
            r.get('css3')
        )for r in artifact_colors])
connection.commit()


# SQL QUERIES

### artifact_metadata Table


#### 1. List all artifacts from the 11th century belonging to Byzantine culture.

In [21]:
cursor.execute(""" 
SELECT id, title, century, culture 
FROM artifact_metadata 
WHERE century LIKE '%11th century%' AND culture LIKE '%Byzantine%'; """) 
results = cursor.fetchall() 
for row in results: 
    print(row)

#### 2. What are the unique cultures represented in the artifacts?

In [22]:
cursor.execute("""
    SELECT DISTINCT culture
    FROM artifact_metadata
    WHERE culture IS NOT NULL
    ORDER BY culture;
""")
results = cursor.fetchall()
print("Unique cultures in artifacts:")
for row in results:
    print(row[0])


Unique cultures in artifacts:
Afghan
African
Algerian
American
American?
Amlash
Assyrian
Australian
Austrian
Austrian?
Aztec
Belgian
Bohemian
British
British, English
British, Scottish
British?
Bulgarian
Burmese
Byzantine
Cambodian
Canadian
Central American
Central Asian
Chinese
Colombian
Coptic?
Costa Rican
Cycladic
Cypriot
Cypriot?
Czech
Dalmatian
Danish
Dogon?
Dutch
Edo
Egyptian
English
Ethiopian
Etruscan
European
Flemish
Flemish?
Franco-Flemish
French
French?
Gandharan
German
German?
Graeco-Roman
Greek
Haitian
Helladic
Hellenistic
Hellenistic or Early Roman
Hispano-Philippine
Honduran
Hungarian
Indian
Indonesian
Iranian
Islamic
Israeli
Italian
Italian, Emilian, Bolognese
Italian, Emilian, Ferrarese
Italian, Emilian, Parmesan
Italian, Lombard
Italian, Lombard, Bergamasque
Italian, Lombard, Milanese
Italian, Marchigian
Italian, Neapolitan
Italian, Northern Italian
Italian, Roman
Italian, Tuscan
Italian, Tuscan, Florentine
Italian, Tuscan, Pisan
Italian, Tuscan, Sienese
Italian, Umbri

#### 3. List all artifacts from the Archaic Period

In [23]:
cursor.execute("""
SELECT id, title, period
FROM artifact_metadata
WHERE period = 'Archaic Period';
""")
results = cursor.fetchall()
print("Artifacts from Archaic Period:")
for row in results:
    print(row)


Artifacts from Archaic Period:
(76741, 'Body Sherd: Face of Woman Looking Left', 'Archaic period')
(77014, 'Body Sherd: Palmette', 'Archaic period')
(77063, 'Body Sherd: Black Gloss', 'Archaic period')
(77064, 'Body Sherd: Dot Register', 'Archaic period')
(77065, 'Body Sherd: Tendrils', 'Archaic period')
(77072, 'Body Sherd: Black-Figure Decoration', 'Archaic period')
(77095, "Rim Sherd: Part of Woman's Head", 'Archaic period')
(77096, 'Body Sherd: Waist of Warrior', 'Archaic period')
(77108, 'Body Sherd: Lower Torso of Draped Figure', 'Archaic period')
(77169, 'Body Sherd: Seated Figure Facing Right', 'Archaic period')
(77411, 'Body Sherd', 'Archaic period')
(77412, 'Body Sherd', 'Archaic period')
(77413, 'Body Sherd: Black Gloss', 'Archaic period')
(77415, 'Body Sherd: Lower Body of Man Carrying Animal', 'Archaic period')
(77416, 'Body Sherd', 'Archaic period')
(77417, 'Body Sherd: Figure Decoration', 'Archaic period')
(77418, 'Body Sherd: Bands on Interior', 'Archaic period')
(77422

#### 4. List artifact titles ordered by accession year in descending order

In [24]:
cursor.execute("""
    SELECT title, accessionyear
    FROM artifact_metadata
    WHERE accessionyear IS NOT NULL
    ORDER BY accessionyear DESC;
""")
results = cursor.fetchall()
print("Artifact titles ordered by accession year (newest first):")
for row in results:
    print(row)


Artifact titles ordered by accession year (newest first):
('View of a Ploughed Field', 2024)
('Landscape with Cephalus and Procris', 2023)
('Two Wooden Houses in the Goudsbloemstraat, Burned December 25, 1682', 2023)
('Fragments of a Siana Cup: Procession of Men with Drinking Horns', 2023)
('Francophone Women of Color and a Young Attendant, Dominica [French Mulatresses of Dominica in their Proper Dress]', 2023)
('Two Women of Color, Dominica [French Mulatress of Dominica and a Negro Woman in their Proper Dress]', 2023)
('Purchasing Fruit [A French Mulatress Purchasing Fruit from a Negro Wench]', 2023)
('Women of Color Bathing and a Voyeur [Mulatresses and Negro Woman Bathing]', 2023)
('Mrs. (Asa) Samuel Hammond (Sarah Dawes Hammond)', 2022)
('(Asa) Samuel Hammond', 2022)
('The Castle at Grave', 2022)
('Study of a Tree', 2022)
('Landscape after Huang Gongwang and Ni Zan', 2022)
('Kneeling Shepherd', 2022)
('Seated Man holding a Drinking Vessel in right hand; facing left; gazing downward

#### 5. How many artifacts are there per department

In [25]:
cursor.execute("""
SELECT department, COUNT(*) AS artifact_count
FROM artifact_metadata
GROUP BY department
ORDER BY artifact_count DESC;
""")
results = cursor.fetchall()
print("Number of artifacts per department:")
for department, count in results:
    print(f"{department}: {count}")


Number of artifacts per department:
Department of Asian Art: 3286
Department of Photographs: 2449
Busch-Reisinger Museum: 1873
Department of Paintings, Sculpture & Decorative Arts: 1213
Department of Ancient and Byzantine Art & Numismatics: 1196
Department of Drawings: 1126
Department of Modern & Contemporary Art: 439
Department of Islamic & Later Indian Art: 409
Department of American Paintings, Sculpture & Decorative Arts: 192
Straus Center for Conservation and Technical Studies: 188
Harvard University Portrait Collection: 129


### artifact_media Table

#### 6. Which artifacts have more than 1 image

In [26]:
cursor.execute("""
SELECT m.title, md.imagecount
FROM artifact_metadata m
JOIN artifact_media md ON m.id = md.objectid
WHERE md.imagecount > 1;
""")
results = cursor.fetchall()
print("Artifacts with more than 1 image:")
for title, imagecount in results:
    print(f"Title: {title}, Images: {imagecount}")


Artifacts with more than 1 image:
Title: Ten Fragments of pottery, Images: 10
Title: Five lamp fragments, Images: 2
Title: Fragment of Egyptian blue on mud from the Palace of Sargon the Great at Khorsabad, Assyria, Images: 4
Title: Branch of Fruiting Pomegranate, Images: 2
Title: End of a River, Images: 8
Title: Journey to India, Images: 4
Title: Honorable Old Man Rock with Text, Images: 3
Title: Early Spring, Images: 4
Title: Peaceful Retreat amidst Mountains and Streams, Images: 2
Title: The Queen, Images: 2
Title: Interplay, Images: 2
Title: Two Peaches and a Faceted Bottle with Auspicious Characters, Images: 2
Title: City Life Album Leaf no. 87, Images: 2
Title: Body Sherd: Black Gloss, Images: 2
Title: Rim Sherd: Part of tondo, Images: 2
Title: Body Sherd: From Cup, Images: 2
Title: Body Sherd: Part of Tondo (?), Images: 2
Title: Study for "Menu for 60th Birthday"; verso: Study for "Menu for 60th Birthday", Images: 2
Title: Rim Sherd: Black Gloss, Images: 2
Title: Body Sherd: Face

#### 7. What is the average rank of all artifacts

In [27]:
cursor.execute("""
SELECT AVG(rank_value) AS average_rank
FROM artifact_media
WHERE rank_value IS NOT NULL;
""")
result = cursor.fetchone()
print(f"Average rank of all artifacts: {result[0]}")

Average rank of all artifacts: 111822.8945


#### 8. Which artifacts have a higher colorcount than mediacount

In [28]:
cursor.execute("""
SELECT m.title, am.colorcount, am.mediacount
FROM artifact_media am
JOIN artifact_metadata m ON am.objectid = m.id
WHERE am.colorcount > am.mediacount;
""")
results = cursor.fetchall()
print("Artifacts where color count is higher than media count:")
for title, colorcount, mediacount in results:
    print(f"Title: {title}, Color Count: {colorcount}, Media Count: {mediacount}")


Artifacts where color count is higher than media count:
Title: Ten Fragments of pottery, Color Count: 8, Media Count: 0
Title: Fragments of Ivory, Lapis, etc. from Samaria, Color Count: 9, Media Count: 0
Title: Five lamp fragments, Color Count: 8, Media Count: 0
Title: Fragment of Egyptian blue on mud from the Palace of Sargon the Great at Khorsabad, Assyria, Color Count: 10, Media Count: 0
Title: SHERD, Color Count: 7, Media Count: 0
Title: Syrian or Neo-Assyrian Cult Figure, Color Count: 10, Media Count: 0
Title: Terracotta Eye Idol, Tel Brak, Color Count: 10, Media Count: 0
Title: Selket, Color Count: 8, Media Count: 0
Title: One of Nine Ceramic fragments, Color Count: 10, Media Count: 0
Title: One of Nine Ceramic fragments, Color Count: 10, Media Count: 0
Title: One of Nine Ceramic fragments, Color Count: 10, Media Count: 0
Title: One of Nine Ceramic fragments, Color Count: 10, Media Count: 0
Title: One of Nine Ceramic fragments, Color Count: 10, Media Count: 0
Title: Dane Hall, Co

#### 9. List all artifacts created between 1500 and 1600

In [29]:
cursor.execute("""
    SELECT title, datebegin, dateend
    FROM artifact_metadata m
    JOIN artifact_media me ON m.id = me.objectid
    WHERE (me.datebegin BETWEEN 1500 AND 1600)
       OR (me.dateend BETWEEN 1500 AND 1600);
""")
results = cursor.fetchall()
print("Artifacts created between 1500 and 1600:")
for row in results:
    print(row)


Artifacts created between 1500 and 1600:
('Landscape after Huang Gongwang and Ni Zan', 1599, 1599)
('Branch of Old Blossoming Plum Tree under Full Moon', 1600, 1800)
('Carp Swimming in a Pond with a Lotus Plant Withered to a Seedpod and a Decaying Leaf', 1570, 1700)
('Two Stalks of Old Bamboo in Spring', 1600, 1800)
('Tawara kasane emaki', 1600, 1632)
('Tawara kasane emaki', 1600, 1632)
('Chrysanthemums and Bamboo', 1600, 1632)
('Landscape with Cephalus and Procris', 1591, 1591)
('Sherd: Fragment of a Dish or Bowl', 1500, 1599)
('Sherd: Fragment of a Vessel', 1200, 1599)
('Sherd: Portion of the Rim of a Vessel, Possibly a Large Jar', 1300, 1599)
('Radha Talking with Her Sakhi on a Terrace, drawing from a Rasikapriya (Handbook for Poetry Connoisseurs) Series', 1600, 1799)
('Funerary Model in the Form of a Single-Story, Tile-Roofed Building, Probably a Guard House, with a Locked Double Door and Two Windows with Grilles', 1400, 1599)
('Pentecost', 1515, 1525)
('Illustrated Story of the Or

#### 10. How many artifacts have no media files

In [30]:
cursor.execute("""
    SELECT COUNT(*)
    FROM artifact_media
    WHERE mediacount = 0 OR mediacount IS NULL;
""")
no_media_count = cursor.fetchone()[0]
print(f"Artifacts with no media files: {no_media_count}")


Artifacts with no media files: 12469


### artifact_colors Table

#### 11. What are all the distinct hues used in the dataset

In [31]:
cursor.execute("""
    SELECT DISTINCT hue
    FROM artifact_colors
    WHERE hue IS NOT NULL
    ORDER BY hue;
""")
results = cursor.fetchall()
print("Distinct hues:")
for row in results:
    print(row[0])


Distinct hues:
Black
Blue
Brown
Green
Grey
Orange
Red
Violet
White
Yellow


#### 12. What are the top 5 most used colors by frequency

In [32]:
cursor.execute("""
SELECT color, COUNT(*) AS frequency
FROM artifact_colors
WHERE color IS NOT NULL
GROUP BY color
ORDER BY frequency DESC
LIMIT 5;
""")
results = cursor.fetchall()
print("Top 5 most used colors:")
for color, freq in results:
    print(f"{color}: {freq}")


Top 5 most used colors:
#c8c8c8: 4613
#e1e1e1: 4417
#afafaf: 4211
#fafafa: 3706
#969696: 3646


#### 13. What is the average coverage percentage for each hue

In [33]:
cursor.execute("""
    SELECT hue, AVG(percent) AS avg_percent
    FROM artifact_colors
    WHERE percent IS NOT NULL
    GROUP BY hue
    ORDER BY avg_percent DESC;
""")
results = cursor.fetchall()
print("Average coverage percentage per hue:")
for hue, avg in results:
    print(f"{hue}: {avg:.2f}%")


Average coverage percentage per hue:
White: 0.35%
Orange: 0.19%
Violet: 0.15%
Green: 0.14%
Black: 0.12%
Grey: 0.11%
Yellow: 0.10%
Red: 0.08%
Blue: 0.08%
Brown: 0.08%


#### 14. List all colors used for a given artifact ID

In [34]:
# Fetch all artifact IDs
import pandas as pd
cursor.execute("SELECT id FROM artifact_metadata;")
results = cursor.fetchall()
for i in results:
  print(i)


(7454,)
(11325,)
(12229,)
(12231,)
(12357,)
(72346,)
(72347,)
(72349,)
(72366,)
(72367,)
(72391,)
(72430,)
(72431,)
(72693,)
(72694,)
(72695,)
(72696,)
(72697,)
(72698,)
(72746,)
(72753,)
(72754,)
(72755,)
(73664,)
(73665,)
(73666,)
(73712,)
(73715,)
(73716,)
(73717,)
(73718,)
(73725,)
(73726,)
(73727,)
(73728,)
(73729,)
(73736,)
(73737,)
(73738,)
(73739,)
(73740,)
(73741,)
(73742,)
(73743,)
(73744,)
(73745,)
(76428,)
(76436,)
(76718,)
(76722,)
(76723,)
(76724,)
(76725,)
(76726,)
(76737,)
(76738,)
(76740,)
(76741,)
(76742,)
(76743,)
(76804,)
(76805,)
(76807,)
(76869,)
(76983,)
(76986,)
(76987,)
(77009,)
(77010,)
(77011,)
(77012,)
(77013,)
(77014,)
(77037,)
(77038,)
(77039,)
(77040,)
(77041,)
(77049,)
(77050,)
(77051,)
(77052,)
(77053,)
(77054,)
(77055,)
(77056,)
(77057,)
(77059,)
(77060,)
(77063,)
(77064,)
(77065,)
(77066,)
(77067,)
(77072,)
(77073,)
(77074,)
(77075,)
(77076,)
(77077,)
(77085,)
(77086,)
(77088,)
(77090,)
(77091,)
(77092,)
(77095,)
(77096,)
(77097,)
(77098,)
(77099,)
(7

In [35]:
artifact_id = int(input("Enter Artifact ID: "))
cursor.execute("""
SELECT color, hue, percent, spectrum, css3
FROM artifact_colors
WHERE objectid = %s;
""", (artifact_id,))
results = cursor.fetchall()
print(f"Colors used for artifact ID {artifact_id}:")
for color, hue, percent, spectrum, css3 in results:
    print(f"{color} | Hue: {hue} | Percent: {percent} | Spectrum: {spectrum} | CSS3: {css3}")


Colors used for artifact ID 73664:
#e1c896 | Hue: Yellow | Percent: 0.7747747747747747 | Spectrum: #ed765a | CSS3: #deb887
#af967d | Hue: Brown | Percent: 0.07171171171171171 | Spectrum: #c25687 | CSS3: #bc8f8f
#7d6464 | Hue: Brown | Percent: 0.06078078078078078 | Spectrum: #8e5ea7 | CSS3: #696969
#323232 | Hue: Grey | Percent: 0.03393393393393394 | Spectrum: #2eb45d | CSS3: #2f4f4f
#967d7d | Hue: Brown | Percent: 0.0203003003003003 | Spectrum: #955ba5 | CSS3: #808080
#64644b | Hue: Green | Percent: 0.016816816816816817 | Spectrum: #59ba4a | CSS3: #696969
#4b4b4b | Hue: Grey | Percent: 0.014714714714714715 | Spectrum: #3db657 | CSS3: #2f4f4f
#7d4b4b | Hue: Red | Percent: 0.006966966966966967 | Spectrum: #b25593 | CSS3: #a0522d


#### 15. What is the total number of color entries in the dataset

In [36]:
cursor.execute("""
SELECT COUNT(*) 
FROM artifact_colors;
""")
total_colors = cursor.fetchone()[0]
print(f"Total number of color entries in the dataset: {total_colors}")


Total number of color entries in the dataset: 85823


### Join-Based Queries

#### 16. List artifact titles and hues for all artifacts belonging to the Byzantine culture.

In [37]:
cursor.execute("""
SELECT m.title, c.hue
FROM artifact_metadata m
JOIN artifact_colors c ON m.id = c.objectid
WHERE m.culture = 'Byzantine';
""")
results = cursor.fetchall()
print("Artifacts from Byzantine culture with their hues:")
for row in results:
    print(f"Title: {row[0]}, Hue: {row[1]}")


Artifacts from Byzantine culture with their hues:
Title: Fragments of Repousse Object, Hue: White
Title: Fragments of Repousse Object, Hue: Yellow
Title: Fragments of Repousse Object, Hue: Green
Title: Fragments of Repousse Object, Hue: Green
Title: Fragments of Repousse Object, Hue: Grey
Title: Fragments of Repousse Object, Hue: Green
Title: Fragments of Repousse Object, Hue: Grey
Title: Fragments of Repousse Object, Hue: Grey
Title: Fragments of Repousse Object, Hue: Grey
Title: Fragments of Repousse Object, Hue: Black
Title: Two Bishop Saints, Hue: White
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Two Bishop Saints, Hue: Grey
Title: Saint John, Hue: Grey
Title: Saint John, Hue: White
Title: Saint John, Hue: Grey
Title: Saint John, Hue: 

#### 17. List each artifact title with its associated hues. 

In [38]:
cursor.execute("""
SELECT md.title, GROUP_CONCAT(ac.hue SEPARATOR ', ') AS hues
FROM artifact_metadata md
JOIN artifact_colors ac ON md.id = ac.objectid
GROUP BY md.title;
""")
results = cursor.fetchall()
print("Artifact titles with their associated hues:")
for title, hues in results:
    print(f"{title}: {hues}")


Artifact titles with their associated hues:
'Alam (finial ornament) for a Battle Standard.  Inscribed in Arabic, "There is no God but God".: Grey, Grey, Grey, Green, Grey, Grey, Green
"Andrew Jackson" Drawn at "Applegreen": Green, Green, Green, Yellow, Green, Green
"Bi"-Shaped Disk with Decoration of Bird and Blossoming Plum Tree on One Side and Butterfly and Blossoming Plant Decor on the Other: Grey, White, Grey, Grey, Grey, Grey, Grey, Grey, Grey, Grey
"Crystal" ball on agate base: Grey, Grey, Grey, Grey, Grey, Grey, Grey, Grey, Grey, Brown
"Eleven" Colophon: Green, Grey, Grey, Grey, Grey, Blue, Grey, Grey, Red, Blue
"Julia": Green, Orange, Green, Green, Green, Green, Yellow
"Lief om Leet" ("Love Leads to Suffering"): Orange, Brown, Brown, Brown, Black, Brown, Green, Black
"Many are the Links..." from Robert Hooke [Text]: Green, Grey, Grey, Grey
"One-Finger Zen" of Monk Chü-chih: Brown, Brown, Red, Grey, Brown, Yellow
"Poems of Spring" (Tosa School): White, Grey, Black, Grey, Grey
"R

#### 18. Get artifact titles, cultures, and media ranks where the period is not null.

In [39]:
cursor.execute("""
SELECT md.title, md.culture, am.rank_value
FROM artifact_metadata md
JOIN artifact_media am ON md.id = am.objectid
WHERE md.period IS NOT NULL;
""")
results = cursor.fetchall()
for title, culture, rank in results:
    print(f"{title} | Culture: {culture} | Rank: {rank}")

Fragments of Ivory, Lapis, etc. from Samaria | Culture: Samarian | Rank: 60227
Fragment of Egyptian blue on mud from the Palace of Sargon the Great at Khorsabad, Assyria | Culture: Assyrian | Rank: 67082
Syrian or Neo-Assyrian Cult Figure | Culture: Syrian | Rank: 125351
Terracotta Eye Idol, Tel Brak | Culture: Sumerian | Rank: 125343
Selket | Culture: Egyptian | Rank: 125341
Tall Scholar's Rock | Culture: Chinese | Rank: 126365
Body Sherd: Black Gloss | Culture: Greek | Rank: 124535
Rim Sherd: Part of tondo | Culture: Greek | Rank: 124537
Body Sherd: From Cup | Culture: Greek | Rank: 124540
Body Sherd: Part of Tondo (?) | Culture: Greek | Rank: 124542
Rim Sherd: Black Gloss | Culture: Greek | Rank: 124536
Body Sherd: Face of Woman Looking Left | Culture: Greek | Rank: 124538
Body Sherd: Part of Garment (?) | Culture: Greek | Rank: 124539
Body Sherd: From Cup | Culture: Greek | Rank: 124541
Sherd: Portion of the Lip of a Vessel, Probably a Jar or Bottle | Culture: Korean | Rank: 119264

#### 19. Find artifact titles ranked in the top 10 that include the color hue "Grey".

In [40]:
cursor.execute("""
SELECT md.title, am.rank_value, ac.hue
FROM artifact_metadata md
JOIN artifact_media am ON md.id = am.objectid
JOIN artifact_colors ac ON md.id = ac.objectid
WHERE ac.hue = 'Grey'
ORDER BY am.rank_value ASC
LIMIT 10;
""")
results = cursor.fetchall()
print("Top 10 ranked artifacts with hue 'Grey':")
for title, rank, hue in results:
    print(f"{title} | Rank: {rank} | Hue: {hue}")


Top 10 ranked artifacts with hue 'Grey':
Seated Chijang Posal (Chinese, Dizang Pusa; Sanskrit, Bodhisattva Ksitigarbha) Flanked by Monk Tomyŏng (Chinese, Daoming) and Demon King Mutok Kuiwang (Chinese, Wudu Guiwang) and Surrounded by the Ten Kings of Hell and Their Retinues | Rank: 14 | Hue: Grey
Stele with Scenes from the Life of the Buddha | Rank: 21 | Hue: Grey
Earthquake from the Legendary History of the Jin'o-ji (Kōnin Shōnin eden) | Rank: 40 | Hue: Grey
Earthquake from the Legendary History of the Jin'o-ji (Kōnin Shōnin eden) | Rank: 40 | Hue: Grey
Earthquake from the Legendary History of the Jin'o-ji (Kōnin Shōnin eden) | Rank: 40 | Hue: Grey
Earthquake from the Legendary History of the Jin'o-ji (Kōnin Shōnin eden) | Rank: 40 | Hue: Grey
The Serf | Rank: 41 | Hue: Grey
The Serf | Rank: 41 | Hue: Grey
The Serf | Rank: 41 | Hue: Grey
The Serf | Rank: 41 | Hue: Grey


#### 20. How many artifacts exist per classification, and what is the average media count for each?

In [41]:
cursor.execute("""
SELECT md.classification, 
       COUNT(*) AS artifact_count, 
       AVG(am.mediacount) AS avg_media_count
FROM artifact_metadata md
JOIN artifact_media am ON md.id = am.objectid
GROUP BY md.classification
ORDER BY artifact_count DESC;
""")
results = cursor.fetchall()
print("Artifacts per classification and average media count:")
for classification, count, avg_media in results:
    print(f"{classification}: Count = {count}, Average Media Count = {avg_media:.2f}")


Artifacts per classification and average media count:
Fragments: Count = 2500, Average Media Count = 0.00
Sculpture: Count = 2500, Average Media Count = 0.01
Photographs: Count = 2500, Average Media Count = 0.00
Paintings: Count = 2500, Average Media Count = 0.00
Drawings: Count = 2500, Average Media Count = 0.00


### Extra SQL queries

#### 21. Show artifacts where accession method contains "purchase

In [42]:
cursor.execute("""
    SELECT title, accessionmethod
    FROM artifact_metadata
    WHERE accessionmethod LIKE '%purchase%';
""")
results = cursor.fetchall()
print("Artifacts with accession method containing 'purchase':")
for row in results:
    print(row)


Artifacts with accession method containing 'purchase':
('Branch of Fruiting Pomegranate', 'Purchase')
('Two Peaches and a Faceted Bottle with Auspicious Characters', 'Purchase')
('Body Sherd: Black Gloss', 'Purchase')
('Rim Sherd: Part of tondo', 'Purchase')
('Body Sherd: From Cup', 'Purchase')
('Body Sherd: Part of Tondo (?)', 'Purchase')
('Rim Sherd: Black Gloss', 'Purchase')
('Body Sherd: Face of Woman Looking Left', 'Purchase')
('Body Sherd: Part of Garment (?)', 'Purchase')
('Body Sherd: From Cup', 'Purchase')
('Body Sherd: Palmette', 'Purchase')
('Body Sherd: Black Gloss', 'Purchase')
('Body Sherd: Dot Register', 'Purchase')
('Body Sherd: Tendrils', 'Purchase')
('Body Sherd: Black gloss', 'Purchase')
('Kylix Fragment: Frontal Torso and Right Hand', 'Purchase')
('Body Sherd: Black-Figure Decoration', 'Purchase')
('Master Sheet', 'Purchase')
('Space and Time Coordinates for November', 'Purchase')
('Graphed Coordinate System for November', 'Purchase')
('Graphed Coordinate System for

#### 22. List all artifacts from a specific department

In [43]:
department_name = "Coins and Medals"
cursor.execute("""
    SELECT title, department
    FROM artifact_metadata
    WHERE department = %s;
""", (department_name,))
results = cursor.fetchall()
print(f"Artifacts in department '{department_name}':")
for row in results:
    print(row[0])


Artifacts in department 'Coins and Medals':


#### 23. Find artifacts that have no description

In [44]:
cursor.execute("""
    SELECT title
    FROM artifact_metadata
    WHERE description IS NULL OR description = '';
""")
results = cursor.fetchall()
print("Artifacts with no description:")
for row in results:
    print(row[0])


Artifacts with no description:
Ten Fragments of pottery
Fragments of Ivory, Lapis, etc. from Samaria
Five lamp fragments
SHERD
Syrian or Neo-Assyrian Cult Figure
Selket
One of Nine Ceramic fragments
One of Nine Ceramic fragments
One of Nine Ceramic fragments
One of Nine Ceramic fragments
One of Nine Ceramic fragments
Dane Hall
Wadsworth House
View of Harvard Yard from Cambridge Common
Holden Chapel, Hollis Hall, University Hall
Appleton Chapel
Interior of Appleton Chapel (with pulpit)
Massachusetts Hall (with figures)
Boat Houses on Charles River
Holden Chapel, Stoughton Hall
Harvard Square (with establishments and horse-drawn trolleys)
Branch of Fruiting Pomegranate
End of a River
Early Spring
Small Landscape with Sailboat and a Windmill on the Right; verso: fragment of a harbor scene with sailboat
Seraphim
Journey to India
Early Spring
Landscape with Slanting Fence, Slope and Underbrush; Two Travellers Leaning Against Fence
Funeral
Peaceful Retreat amidst Mountains and Streams
The Qu

#### 24. Show artifacts ordered by their object ID

In [45]:
cursor.execute("""
    SELECT id, title
    FROM artifact_metadata
    ORDER BY id ASC;
""")
results = cursor.fetchall()
print("Artifacts ordered by object ID:")
for row in results:
    print(row)

Artifacts ordered by object ID:
(7454, 'Ten Fragments of pottery')
(11325, 'Fragments of Ivory, Lapis, etc. from Samaria')
(12229, 'Five lamp fragments')
(12231, 'Fragment of Egyptian blue on mud from the Palace of Sargon the Great at Khorsabad, Assyria')
(12357, 'SHERD')
(72346, 'Syrian or Neo-Assyrian Cult Figure')
(72347, 'Terracotta Eye Idol, Tel Brak')
(72349, 'Selket')
(72366, 'One of Nine Ceramic fragments')
(72367, 'One of Nine Ceramic fragments')
(72391, 'One of Nine Ceramic fragments')
(72430, 'One of Nine Ceramic fragments')
(72431, 'One of Nine Ceramic fragments')
(72693, 'Dane Hall')
(72694, 'Wadsworth House')
(72695, 'View of Harvard Yard from Cambridge Common')
(72696, 'Holden Chapel, Hollis Hall, University Hall')
(72697, 'Appleton Chapel')
(72698, 'Interior of Appleton Chapel (with pulpit)')
(72746, 'Massachusetts Hall (with figures)')
(72753, 'Boat Houses on Charles River')
(72754, 'Holden Chapel, Stoughton Hall')
(72755, 'Harvard Square (with establishments and horse

#### 25. Count how many artifacts have a non-null period

In [46]:
cursor.execute("""
    SELECT COUNT(*)
    FROM artifact_metadata
    WHERE period IS NOT NULL;
""")
count = cursor.fetchone()[0]
print(f"Number of artifacts with a defined period: {count}")


Number of artifacts with a defined period: 2899
